#  Lexical Decision Task Experiments Data Analysis

## Visualizing Participants Data

In [123]:
import os

import pandas as pd
import numpy as np
import plotly.express as px

from scipy.stats import (
    mode,
    mannwhitneyu,
    chisquare,
    kstest,
    shapiro,
    wilcoxon
)


In [2]:
data = pd.read_csv('data/LD_preprocessed_data.csv')

In [4]:
MAPPING = {
    'modality': {
        0: 'visual',
        1: 'auditory'
    },
    'is_word': {
        0: 'pseudowords',
        1: 'words'
    }
}

In [124]:
def show_boxplot(data:pd.DataFrame, modality: int, is_word: int, target='rt') -> None:
    '''
    A function to display boxplots for participants RTs (`target`) in `modality` for `is_word`
    '''
    fig = px.box(
            data[
                (data['modality'] == modality)
                &(data['is_word'] == 1)
             ],
             x="experiment_id",
             y="rt",
             labels={
                     "rt": "reaction time (s)",
                     "experiment_id": "subject ID",
                 },
             color='experiment_id',
             title=f"""Reaction times by participant ({MAPPING['modality'][modality]} experiment,
 {MAPPING['is_word'][is_word]})"""
             ).update_xaxes(nticks=len(data['subject'].unique())).update_layout(showlegend=False)
    fig.show()
    
[show_boxplot(data, m, s) for m in (0, 1) for s in (1, 0)]
print()

## Error Analysis

In [105]:
def error_info(data:pd.DataFrame, modality: int, is_word: int) -> pd.DataFrame:
    '''
    A function to get info dataframe with base statistics for errors in `modality` for `is_word`
    '''
    errors = data[
        (data['modality'] == modality)
        &(data['is_correct'] == 0)
    ].groupby(['subject', 'is_word']).count()[['word']]
    
    statistics = errors.loc[pd.IndexSlice[:, is_word], :].describe()
    Total = pd.Series(
        np.sum(errors.loc[pd.IndexSlice[:, is_word], :]['word']),
        index=['total'],
    )
    Median = pd.Series(
        np.median(errors.loc[pd.IndexSlice[:, is_word], :]['word']),
        index=['median']
    )
    Mode = pd.Series(
        mode(errors.loc[pd.IndexSlice[:, is_word], :]['word'], keepdims=False),
        index=['mode', 'mode_counts'])
    statistics = pd.concat([Total, statistics, Median, Mode]).fillna(0)
    statistics['word'] = (statistics['word'] + statistics[0])
    return statistics.drop(columns=0)

In [107]:
error_data = pd.concat(
    [
        error_info(data, m, s).rename(
            columns={'word':f"{MAPPING['modality'][m]}:{MAPPING['is_word'][s]}"}
        ).round(2) for s in (1, 0) for m in (0, 1)
    ],
    axis=1
)
display(error_data)

visual:words  auditory:words  visual:pseudowords  \
total               42.00          101.00               60.00   
count               14.00           21.00               17.00   
mean                 3.00            4.81                3.53   
std                  2.39            3.28                3.26   
min                  1.00            1.00                1.00   
25%                  1.25            3.00                1.00   
50%                  2.50            5.00                2.00   
75%                  3.75            6.00                5.00   
max                 10.00           13.00               13.00   
median               2.50            5.00                2.00   
mode                 1.00            1.00                1.00   
mode_counts          4.00            4.00                6.00   

             auditory:pseudowords  
total                      208.00  
count                       23.00  
mean                         9.04  
std                          9.37  
min                          1.00  
25%                          3.00  
50%                          5.00  
75%                         10.50  
max                         33.00  
median                       5.00  
mode                         3.00  
mode_counts                  4.00

## Stimuli Features Correlation Analysis

In [129]:
FEATURES = {
    0: { # visual modality
        1: [ # words
            'Freq(ipm)',
            'MedianValency',
            'MeanValency',
            'OLD20',
            'OUP',
            'LengthOrth',
            'NormOLD'
        ],
        0: [ # pseudowords
            'OLD20',
            'OUP',
            'LengthOrth',
            'NormOLD'
        ],
    },
    1: { # auditory modality
        1: [ # words
            'Freq(ipm)',
            'MedianValency',
            #'MeanValency',
            'PLD20',
            'PUP',
            'LengthPhon',
            'NormPLD',
            'Duration',
        ],
        0: [ # pseudowords
            'PLD20',
            'PUP',
            'LengthPhon',
            'NormPLD',
            'Duration',
        ],
    }
}
TARGET = [
    'rt',
    'rtz',
    'rtz_subject',
    'rtz_word',
]

In [131]:
def get_corr_matrix(data:pd.DataFrame, modality: int, is_word: int, method='spearman') -> pd.DataFrame:
    '''
    A function to get correlation matrix in `modality` for `is_word` as a dataframe
    '''
    return data[(data['modality'] == modality)&(data['is_word'] == is_word)][
        TARGET + FEATURES[modality][is_word]
    ].corr(method=method)

def display_corr_matrix(
    data:pd.DataFrame,
    modality: int,
    is_word: int,
    method='spearman',
    text_auto='.2f',
    color_scale='greys'
) -> None:
    
    fig = px.imshow(
        get_corr_matrix(
            data, 
            modality, 
            is_word, 
            method=method
        ),
        text_auto=text_auto,
        color_continuous_scale=color_scale,
        title=f"""Feature correlation matrix ({MAPPING['modality'][modality]} experiment,
 {MAPPING['is_word'][is_word]})"""
    )
    fig.show()
    
[display_corr_matrix(data, m, s) for m in (0, 1) for s in (1, 0)]
print()

## Sample Distribution Visualization

### Cutting off all outliers

In [137]:
data = data[data['is_outlier'] == 0]

### Visualizing stimluli RT distributions for the two modalities

In [147]:
def change_lables(t):
    t.update(
        name = MAPPING['is_word'][int(t.name)],
        legendgroup = MAPPING['is_word'][int(t.name)],
        hovertemplate = t.hovertemplate.replace(t.name, MAPPING['is_word'][int(t.name)])
    )

def change_annotations(t):
    t.update(
        text = t.text[:t.text.index('=') + 1] + MAPPING['modality'][int(t.text[t.text.index('=') + 1:])]
    )


fig = px.histogram(
    data.sort_values(by='modality'),
    x="rt",
    labels={
         "rt": "reaction time (s)",
        'is_word': 'stimulus type',
         },
    color='is_word',
    barmode='overlay',
    histnorm='probability density',
    facet_col='modality',
    ).update_layout(
    yaxis_title="probability density"
).for_each_trace(change_lables).for_each_annotation(change_annotations)

fig.show()

In [149]:
def change_lables(t):
    t.update(
        name = MAPPING['is_word'][int(t.name)],
        legendgroup = MAPPING['is_word'][int(t.name)],
        hovertemplate = t.hovertemplate.replace(t.name, MAPPING['is_word'][int(t.name)])
    )

def change_annotations(t):
    t.update(
        text = t.text[:t.text.index('=') + 1] + MAPPING['modality'][int(t.text[t.text.index('=') + 1:])]
    )


fig = px.ecdf(
    data.sort_values(by='modality'),
    x="rt",
    labels={
         "rt": "reaction time (s)",
        'is_word': 'stimulus type',
         },
    color='is_word',
    facet_col='modality',
    ).update_layout(
    yaxis_title="ECDF"
).for_each_trace(change_lables).for_each_annotation(change_annotations)

fig.show()

### Visualizing modality RT distributions for the two stimuli types

In [150]:
def change_lables(t):
    t.update(
        name = MAPPING['modality'][int(t.name)],
        legendgroup = MAPPING['modality'][int(t.name)],
        hovertemplate = t.hovertemplate.replace(t.name, MAPPING['modality'][int(t.name)])
    )

def change_annotations(t):
    t.update(
        text = t.text[:t.text.index('=') + 1] + MAPPING['is_word'][int(t.text[t.text.index('=') + 1:])]
    )


fig = px.histogram(
    data.sort_values(by='is_word', ascending=False),
    x="rt",
    labels={
         "rt": "reaction time (s)",
        'is_word': 'stimulus type',
         },
    color='modality',
    barmode='overlay',
    histnorm='probability density',
    facet_col='is_word',
    ).update_layout(
    yaxis_title="probability density"
).for_each_trace(change_lables).for_each_annotation(change_annotations)

fig.show()

In [151]:
def change_lables(t):
    t.update(
        name = MAPPING['modality'][int(t.name)],
        legendgroup = MAPPING['modality'][int(t.name)],
        hovertemplate = t.hovertemplate.replace(t.name, MAPPING['modality'][int(t.name)])
    )

def change_annotations(t):
    t.update(
        text = t.text[:t.text.index('=') + 1] + MAPPING['is_word'][int(t.text[t.text.index('=') + 1:])]
    )


fig = px.ecdf(
    data.sort_values(by='is_word', ascending=False),
    x="rt",
    labels={
         "rt": "reaction time (s)",
        'is_word': 'stimulus type',
         },
    color='modality',
    facet_col='is_word',
    ).update_layout(
    yaxis_title="ECDF"
).for_each_trace(change_lables).for_each_annotation(change_annotations)

fig.show()

## Statistical Tests

### Checking normality

In [163]:
def normality(data:pd.DataFrame, modality: int, is_word: int, target='rt') -> pd.Series:
    '''
    A function to check if the distribution of `target` is normal in `modality` for `is_word`
    '''
    return pd.Series(
        shapiro(data[(data['modality'] == modality)&(data['is_word'] == is_word)][target]),
        index=(f'{target}:statistic', f'{target}:p-value')
    )

normality_tests = pd.concat(
    [
        pd.concat(
            [
                normality(data, m, s, target=rt).rename(
                    f"{MAPPING['modality'][m]}:{MAPPING['is_word'][s]}"
                ).round(4) for s in (1, 0) for m in (0, 1)
            ],
            axis=1
        ) for rt in TARGET
    ],
    axis=0
)

display(normality_tests)

visual:words  auditory:words  visual:pseudowords  \
rt:statistic                 0.9705          0.9737              0.9654   
rt:p-value                   0.0000          0.0000              0.0000   
rtz:statistic                0.9950          0.9926              0.9944   
rtz:p-value                  0.0000          0.0000              0.0000   
rtz_subject:statistic        0.9694          0.9573              0.9820   
rtz_subject:p-value          0.0000          0.0000              0.0000   
rtz_word:statistic           0.9745          0.9699              0.9637   
rtz_word:p-value             0.0000          0.0000              0.0000   

                       auditory:pseudowords  
rt:statistic                         0.9764  
rt:p-value                           0.0000  
rtz:statistic                        0.9840  
rtz:p-value                          0.0000  
rtz_subject:statistic                0.9776  
rtz_subject:p-value                  0.0000  
rtz_word:statistic                   0.9707  
rtz_word:p-value                     0.0000

### Comparing two samples

In [176]:
def MVU_test(data:pd.DataFrame, fixed: str, value: int, target='rt', alpha=0.01) -> pd.DataFrame:
    '''
    A function to perform Mann-Whitney statistic test.
    Arguments:
        - data: the dataset
        - fixed: fixed feature, `modality` of `is_word`
        - value: value of the fixed feature, 0 or 1
        - target: target variable (optional, default 'rt')
        - alpha: level of significance (optional, default 0.01)
    '''
    variable = 'modality' if fixed == 'is_word' else 'is_word'
    statistic, pvalue = mannwhitneyu(
        data[(data[fixed] == value)&(data[variable] == 0)][target], 
        data[(data[fixed] == value)&(data[variable] == 1)][target],
        alternative='greater'
    )
    return pd.Series(
        (statistic, pvalue, pvalue <= alpha),
        index=(
            f'{target}:statistic',
            f'{target}:p-value',
            f'{target}:significance',
        ),
    )

def MVU_test(data:pd.DataFrame, fixed: str, value: int, target='rt', alpha=0.01) -> pd.DataFrame:
    '''
    A function to perform Mann-Whitney statistic test.
    H_0:
        forall x in data[fixed=value][var=n], y in data[fixed=value][var=m]: P(x < y) = 1/2
    H_1:
        P(x < y) > 1/2
    Expected results: for value n of fixed feature RTs are statistically greater
        n is 1 for modality and 0 for stimulus type; m is the opposite
    Arguments:
        - data: the dataset
        - fixed: fixed feature, `modality` of `is_word`
        - value: value of the fixed feature, 0 or 1
        - target: target variable (optional, default 'rt')
        - alpha: level of significance (optional, default 0.01)
    '''
    var = variable(fixed)
    greater = VALUES[var][1]
    
    statistic, pvalue = mannwhitneyu(
        data[(data[fixed] == value)&(data[var] == greater)][target], 
        data[(data[fixed] == value)&(data[var] == abs(greater - 1))][target],
        alternative='greater'
    )
    return pd.Series(
        (statistic, pvalue, pvalue <= alpha),
        index=(
            f'{target}:statistic',
            f'{target}:p-value',
            f'{target}:significance',
        ),
    )


VALUES = {
    'modality': (0, 1),
    'is_word': (1, 0)
}
def variable(fixed: str) -> str:
    return 'modality' if fixed == 'is_word' else 'is_word'

mvu_tests = pd.concat(
    [
        pd.concat(
            [
                MVU_test(data, fixed, val, target=rt).rename(
                    f"{MAPPING[fixed][val]}, " + 
                        f"{MAPPING[variable(fixed)][VALUES[variable(fixed)][1]]}>" +
                        f"{MAPPING[variable(fixed)][VALUES[variable(fixed)][0]]}"
                ) for fixed in ('modality', 'is_word') for val in VALUES[fixed]
            ],
            axis=1
        ).round(4) for rt in TARGET
    ],
    axis=0
)

display(mvu_tests)

visual, pseudowords>words  \
rt:statistic                             5040795.0   
rt:p-value                                     0.0   
rt:significance                               True   
rtz:statistic                            3659215.0   
rtz:p-value                                    1.0   
rtz:significance                             False   
rtz_subject:statistic                    5449149.0   
rtz_subject:p-value                            0.0   
rtz_subject:significance                      True   
rtz_word:statistic                       3894732.0   
rtz_word:p-value                          0.990728   
rtz_word:significance                        False   

                         auditory, pseudowords>words words, auditory>visual  \
rt:statistic                               6844639.0              9270612.0   
rt:p-value                                       0.0                    0.0   
rt:significance                                 True                   True   
rtz:statistic                              4570754.0              4559373.0   
rtz:p-value                                      1.0               0.955057   
rtz:significance                               False                  False   
rtz_subject:statistic                      7239309.0              4374112.0   
rtz_subject:p-value                              0.0               0.999994   
rtz_subject:significance                        True                  False   
rtz_word:statistic                         5014018.0              4551220.0   
rtz_word:p-value                            0.894182               0.965159   
rtz_word:significance                          False                  False   

                         pseudowords, auditory>visual  
rt:statistic                                8740778.0  
rt:p-value                                        0.0  
rt:significance                                  True  
rtz:statistic                               4300651.0  
rtz:p-value                                  0.953207  
rtz:significance                                False  
rtz_subject:statistic                       4439342.0  
rtz_subject:p-value                          0.337342  
rtz_subject:significance                        False  
rtz_word:statistic                          4381166.0  
rtz_word:p-value                             0.677127  
rtz_word:significance                           False

In [179]:
def KS_test(data:pd.DataFrame, fixed: str, value: int, target='rt', alpha=0.01) -> pd.DataFrame:
    '''
    A function to perform Mann-Whitney statistic test.
    H_0:
        forall x: F(x) <= G(y), where
            data[fixed=value][var=n] ~ F
            data[fixed=value][var=m] ~ G
    H_1:
        exists x: F(x) > G(x)
    Expected results: cdf F for n is indeed less, than cdf G for m for all RTs
        n is 1 for modality and 0 for stimulus type; m is the opposite
    Arguments:
        - data: the dataset
        - fixed: fixed feature, `modality` of `is_word`
        - value: value of the fixed feature, 0 or 1
        - target: target variable (optional, default 'rt')
        - alpha: level of significance (optional, default 0.01)
    '''
    var = variable(fixed)
    greater = VALUES[var][1]
    
    statistic, pvalue = kstest(
        data[(data[fixed] == value)&(data[var] == greater)][target], 
        data[(data[fixed] == value)&(data[var] == abs(greater - 1))][target],
        alternative='greater',
        method='asymp'
    )
    return pd.Series(
        (statistic, pvalue, pvalue <= alpha),
        index=(
            f'{target}:statistic',
            f'{target}:p-value',
            f'{target}:significance',
        ),
    )


VALUES = {
    'modality': (0, 1),
    'is_word': (1, 0)
}

def variable(fixed: str) -> str:
    return 'modality' if fixed == 'is_word' else 'is_word'

ks_tests = pd.concat(
    [
        pd.concat(
            [
               KS_test(data, fixed, val, target=rt).rename(
                    f"{MAPPING[fixed][val]}, " + 
                        f"{MAPPING[variable(fixed)][VALUES[variable(fixed)][1]]}>" +
                        f"{MAPPING[variable(fixed)][VALUES[variable(fixed)][0]]}"
                ) for fixed in ('modality', 'is_word') for val in VALUES[fixed]
            ],
            axis=1
        ).round(4) for rt in TARGET
    ],
    axis=0
)

display(ks_tests)

visual, pseudowords>words  \
rt:statistic                              0.001071   
rt:p-value                                0.995683   
rt:significance                              False   
rtz:statistic                             0.088464   
rtz:p-value                                    0.0   
rtz:significance                              True   
rtz_subject:statistic                     0.000683   
rtz_subject:p-value                       0.997997   
rtz_subject:significance                     False   
rtz_word:statistic                        0.042939   
rtz_word:p-value                          0.005076   
rtz_word:significance                         True   

                         auditory, pseudowords>words words, auditory>visual  \
rt:statistic                                     0.0                    0.0   
rt:p-value                                       1.0                    1.0   
rt:significance                                False                  False   
rtz:statistic                               0.096629               0.031226   
rtz:p-value                                      0.0               0.049407   
rtz:significance                                True                  False   
rtz_subject:statistic                       0.000009               0.067721   
rtz_subject:p-value                         0.999991               0.000001   
rtz_subject:significance                       False                   True   
rtz_word:statistic                          0.039743               0.039706   
rtz_word:p-value                            0.006179                0.00781   
rtz_word:significance                           True                   True   

                         pseudowords, auditory>visual  
rt:statistic                                      0.0  
rt:p-value                                        1.0  
rt:significance                                 False  
rtz:statistic                                0.048206  
rtz:p-value                                   0.00097  
rtz:significance                                 True  
rtz_subject:statistic                        0.017371  
rtz_subject:p-value                          0.401807  
rtz_subject:significance                        False  
rtz_word:statistic                           0.039812  
rtz_word:p-value                             0.008748  
rtz_word:significance                            True

## Stimuli Diffuculty Hierarchy

In [201]:
def get_ranks(data:pd.DataFrame, modality: int, is_word: int, target='rt') -> pd.DataFrame:
    '''
    A function to get a dataframe of sorted stimuli of type `is_word` by their average `target` score
    '''
    N_STIMULI = len(data[(data['is_word'] == is_word)]['word'].unique())
    ranks = data[
            (data['modality'] == modality)&(data['is_word'] == is_word)
        ].groupby(['word'])[[target]].mean().sort_values(by=target).rename(
            columns={target:f'{target}_{modality}'}
    )
    #ranks[f'R_{modality}'] = [i for i in range(1, N_STIMULI + 1)]
    return ranks

def compare_ranks(data:pd.DataFrame, is_word: int, target='rt', alpha=0.01):
    '''
    A function to check if two arrangements are statistically identical with Wilcoxon test
    '''
    ranks = pd.merge(
        *[get_ranks(data, modality, is_word, target) for modality in (0, 1)],
        on='word',
        how='left'
    )
    statistic, pvalue = wilcoxon(ranks[target+'_0'], ranks[target+'_1'])
    return pd.Series(
        (statistic, pvalue, pvalue <= alpha),
        index=(
            f'{target}:statistic',
            f'{target}:p-value',
            f'{target}:significance',
        ),
    )

    
     

rank_tests = pd.concat(
    [
        pd.concat(
            [
                compare_ranks(data, s, target=rt).rename(
                    f"{MAPPING['is_word'][s]}"
                ) for s in (1, 0)
            ],
            axis=1
        ).round(4) for rt in TARGET
    ],
    axis=0
)

display(rank_tests)

words pseudowords
rt:statistic                   0.0         0.0
rt:p-value                     0.0         0.0
rt:significance               True        True
rtz:statistic               3981.0      4685.0
rtz:p-value               0.013476    0.285993
rtz:significance             False       False
rtz_subject:statistic       3837.0      5032.0
rtz_subject:p-value       0.005813    0.707713
rtz_subject:significance      True       False
rtz_word:statistic          3346.0      4043.0
rtz_word:p-value          0.000186     0.01891
rtz_word:significance         True       False